In [1]:
from common import *

import xml.etree.ElementTree as ET
from pymongo import MongoClient
import pymongo

from pymystem3 import Mystem

Slow version of gensim.models.doc2vec is being used


In [2]:
fname = join(join(DATA_FOLDER, 'rawdata'), 'all_docs_raw.txt')

In [3]:
# all_docs = glob(join(DATA_FOLDER, 'rawdata') + '/**/*.xml', recursive=True)
# all_docs = sorted(all_docs)
# with open(fname, mode='wt', encoding='utf-8') as f:
#     f.write('\n'.join(all_docs))

In [4]:
with open(fname, mode='r', encoding='utf-8') as f:
    all_docs = f.read().splitlines()

FileNotFoundError: [Errno 2] No such file or directory: '../data/rawdata/all_docs_raw.txt'

In [ ]:
len(all_docs)

In [ ]:
def get_node(root, name, lang='ru'):
    for node in root.iter(name):
        if 'lang' in node.attrib:
            if node.attrib['lang'].lower() == lang:
                return node
        else:
            return node

In [ ]:
def parse_xml(fname, mstem, lemmatize=True, save_raw=True):
    doc = {}

    with open(fname, 'r', encoding='utf8') as f:
        text = f.read()
        text = text.replace('&deg', 'deg')
    
    try:
        root = ET.fromstring(text)
    except:
        print(fname)
        return
    
    doc.update(root.attrib)

    raw_texts = {}
    
    SDOBI = get_node(root, 'SDOBI')
    if SDOBI is not None:
        node = SDOBI.find('./B500/ru-b540/ru-b542')
        if node is not None:
            raw_texts['name'] = node.text.lower()
        else:
            print(fname)            
    else:
        print('no SDOBI: ' + fn)

    node = get_node(root, 'abstract')
    if node is not None:
        raw_texts['abstract'] = ' '.join(node.itertext()).lower()

    if SDOBI is not None:
        node = SDOBI.find('./B500/B560/ru-b560')
        if node is not None:
            doc['ru-b560'] = ' '.join(node.itertext())

    node = get_node(root, 'description')
    if node is not None:
        raw_texts['description'] = ' '.join(node.itertext()).lower()

    node = get_node(root, 'claims')
    if node is not None:
        raw_texts['claims'] = ' '.join(node.itertext()).lower()        
    
    
    for k,v in raw_texts.items():
        if save_raw:
            doc[k + '_raw'] = v
        if lemmatize:
            doc[k] = ''.join(mstem.lemmatize(v))    
    
    return doc

# Test

In [7]:
afile = '../data/rawdata/2016/RU/A/20161227/2015116494/2015116494.xml'
c1file = '../data/rawdata/2016/RU/C1/20161227/0002605713/0002605713.xml'
c2file = '../data/rawdata/2016/RU/C2/20160127/0002573901/0002573901.xml'
ufile = '../data/rawdata/2016/RU/U1/20161210/0000166582/0000166582.xml'

In [8]:
mstem = Mystem()
doc = parse_xml(c2file, mstem)

Installing mystem to /home/administrator/.local/bin/mystem from http://download.cdn.yandex.net/mystem/mystem-3.0-linux3.1-64bit.tar.gz


In [21]:
print(doc['description'])

область техника настоящий изобретение относиться к способ получение поверхностный покрытие на основа поливинилхлорид (пвх), содержать слой износ на основа пвх и слой на основа поливиниловый спирт. предшествующий уровень техника поверхностный покрытие на основа пвх широко применять для декорирование сооружение, дом или транспортный средство. однако поверхностный покрытие на основа пвх обладать недостаток высвобождение летучий органический соединение (лос), некоторый из который токсичный. для уменьшение или предотвращение высвобождение лос быть предлагать замещать летучий соединение нелетучий соединение. однако этот приводить к значительный снижение жесткость поверхностный покрытие, в тот время как жесткость являться важный требование для упругий поверхностный покрытие, особенно напольный покрытие. также быть предлагать применение полиэфирный или полиамидный слой в качество защитный слой или в качество промежуточный слой в многослойный поверхностный покрытие. поливинилспиртовой (пвс) сло

In [9]:
doc

{'abstract': 'изобретение относиться к способ получение поверхностный покрытие, содержать этап обеспечение слой износ на основа пвх (1), по существо, свободный от неорганический наполнитель, нанесение на упоминать слой на основа пвх (1) композиция верхний покрытие, содержать поливиниловый спирт (пвс) и соединение силан, содержать по меньший мера один аминогруппа, нагревание упоминать слой на основа пвх (1) и упоминать композиция верхний покрытие при температура, эквивалентный или превосходить 150°c, для образование верхний покрытие слой износ (2). результат являться получение поверхностный покрытие, сочетать свойство физический устойчивость и свойство химический и газовый барьер. 2 н. и 12 з.п. ф-лы, 4 ил., 6 табла.\n',
 'abstract_raw': 'изобретение относится к способу получения поверхностного покрытия, содержащему этапы обеспечения слоя износа на основе пвх (1), по существу, свободного от неорганических наполнителей, нанесения на упомянутый слой на основе пвх (1) композиции верхнего п

# Fill database with data

In [5]:
client = MongoClient()
db = client.fips

In [6]:
# result = db.patents.create_index([('doc-number', pymongo.ASCENDING),
#                                    ('kind', pymongo.ASCENDING),
#                                    ('country', pymongo.ASCENDING),
#                                    ('date-publ', pymongo.ASCENDING)], unique=True)
# sorted(list(db.patents.index_information()))

In [6]:
def save_to_mongodb(doc_list):
    client = MongoClient()
    db = client.fips
    patents = db.patents
    
    mstem = Mystem()
    
    for fn in doc_list:
        doc = parse_xml(fn, mstem, True, True)
        if doc is not None:
            patents.insert_one(doc)

In [12]:
len(all_docs)//(cpu_count*100)

395

In [ ]:
split_on = len(all_docs)//(cpu_count*100)

for i,sub_docs in enumerate(tqdm(np.array_split(all_docs, split_on))):
    ! rm -f ../data/out
    ! echo {i} >> ../data/out
    
    parallelizer = Parallel(n_jobs=cpu_count)

    # this iterator returns the functions to execute for each task
    tasks_iterator = ( delayed(save_to_mongodb)(list_block) for 
                      list_block in grouper(100, sub_docs) ) 
    result = parallelizer( tasks_iterator )

 21%|██▏       | 84/395 [23:52<54:56, 10.60s/it]  

../data/rawdata/1999/RU/C1/19990220/0002126409/0002126409.xml


 93%|█████████▎| 369/395 [2:40:03<29:43, 68.61s/it]t]

../data/rawdata/2015/Patents/xrfd201503/DOC/RUNWC2/000/000/002/560/425/document.xml


100%|██████████| 395/395 [2:58:26<00:00, 44.67s/it]


In [16]:
# docs = []
# mstem = Mystem()

# for fn in tqdm(all_docs):
#     doc = parse_xml(fn, mstem, False, False)
#     if doc is not None:
#         patents.insert_one(doc)
# #         docs.append(doc)

In [ ]:
# patents.insert_many(docs)

# Analyze data

In [7]:
from bson.son import SON
from pprint import pprint

In [7]:
pipeline = [
     {"$group": {"_id": "$kind", "count": {"$sum": 1}}},
     {"$sort": SON([("count", -1), ("_id", -1)])}
 ]

pprint.pprint(list(db.patents.aggregate(pipeline)))

[{'_id': 'A ', 'count': 438164},
 {'_id': 'C1', 'count': 380857},
 {'_id': 'C2', 'count': 214003},
 {'_id': 'U1', 'count': 167301},
 {'_id': 'A1', 'count': 60184},
 {'_id': 'C ', 'count': 2527},
 {'_id': 'C9', 'count': 1372},
 {'_id': 'A2', 'count': 1028},
 {'_id': 'A3', 'count': 824},
 {'_id': 'U8', 'count': 650},
 {'_id': 'C8', 'count': 13},
 {'_id': 'A4', 'count': 13},
 {'_id': 'A8', 'count': 4}]


In [9]:
db.patents.find({ 'ru-b560': {'$exists': True}}).count()

591782

In [13]:
pipeline = [
    {"$match":{"ru-b560":{'$exists': True}}},
    {"$group": {"_id": "$kind", "count": {"$sum": 1}}},
    {"$sort": SON([("count", -1), ("_id", -1)])}
 ]

pprint.pprint(list(db.patents.aggregate(pipeline)))

[{'_id': 'C1', 'count': 363083},
 {'_id': 'C2', 'count': 213916},
 {'_id': 'A1', 'count': 10647},
 {'_id': 'C ', 'count': 2042},
 {'_id': 'C9', 'count': 1365},
 {'_id': 'A3', 'count': 398},
 {'_id': 'A2', 'count': 305},
 {'_id': 'C8', 'count': 12},
 {'_id': 'A4', 'count': 9},
 {'_id': 'U8', 'count': 4},
 {'_id': 'U1', 'count': 1}]


In [54]:
topn = db.patents.find({'kind': 'C1', 'ru-b560': {'$exists': True}}, 
                       {'ru-b560': 1, "_id": 0}).skip(24300).limit(100)
pprint(list(topn))

[{'ru-b560': 'Патент GB N 2024829, C 07G 7/00, \n\n1980.'},
 {'ru-b560': 'Авторское свидетельство СССР N 1404050, A 23 K 1/00, 1988 г.'},
 {'ru-b560': 'Авторское свидетельство СССР N 1284240, кл. C 21C 7/10,\n'
             '\n'
             ' 1985.'},
 {'ru-b560': 'Авторское свидетельство СССР N 1809185, кл. F 15B 15/22, '
             '1990.Авторское свидетельство СССР N 697763, кл. F 16F 9/48, '
             '1979.'},
 {'ru-b560': 'Преображенский В.И. Полупроводниковые выпрямители. М.: '
             'Энергоатомиздат, 1986, с.41-42.Авторское свидетельство СССР \n'
             '\n'
             'N 1684894, кл. H 02P 1/28, 1989.'},
 {'ru-b560': '1. Авторское свидетельство СССР N 415130, кл. B 23P 19/02, '
             '1974.2. Авторское свидетельство СССР N 1234152, кл. B 23P '
             '19/02,\n'
             ' 1986.'},
 {'ru-b560': 'Патент США N 4795248, кл. G 02C 7/04, 1989.'},
 {'ru-b560': 'ГОСТ 4347-77, с.2.'},
 {'ru-b560': 'Авторское свидетельство СССР N 286159, кл. C 03B 3

In [139]:
for doc in topn:
    splited = doc['ru-b560'].split(',')
    

In [146]:
topn = db.patents.find({}, {'doc-number': 1, "_id": 0})
numbers = []
for doc in topn:
    numbers.append(doc['doc-number'])

In [155]:
len([n for n in numbers if len(n) > 8])

709242

In [160]:
str56 = 'US 5262019 A1, 16.11.93. СПИЦЫН В.И., КУЗИНА А.Ф. Технеций. - М.: Наука, 1981, с.42-53, \n\n120-122. ГОЛЬДАНСКИЙ В.Н. Новые элементы в периодической системе Д.И.Менделеева. - М.: АТОМИЗДАТ, 1964, с.124-126. RU 2029400 C1, 20.02.95. US 5156722 A1, 20.10.92. US 5183541 A1, 02.02.93.'

In [90]:
import re

p = re.compile('(?:RU|SU|ru|su)\s+\d{1,}\s+(?:C1|C2|U1|A1|C |C9|A2|A3|U8|C8|A4|A8)')
# p = re.compile('(?:RU|SU|ru|su)\s+\d{1,}')

# print(p.findall('sdfsdg    RU    2029400 C1, 20.02.95. US 5156722 A1'))


topn = db.patents.find({'ru-b560': {'$exists': True}}, 
                       {'ru-b560': 1})

regexed = {}
for doc in topn:
    found = p.findall(doc['ru-b560'])
    if len(found):
        regexed[str(doc['_id'])] = found

In [91]:
len(regexed)

328830

In [88]:
len(regexed2)

439803

In [92]:
diff = list(set(regexed2.keys()).symmetric_difference(regexed.keys()))

In [93]:
len(diff)

110973

In [94]:
for el in diff:
    print(regexed2[el])

['RU 2195024']
['SU 1321360']
['RU 2087528']
['RU 2001112160']
['RU 2296827']
['SU 986312', 'SU 1209059']
['SU 1675244', 'SU 629178']
['SU 1085606']
['SU 706644', 'SU 992898']
['SU 940771', 'RU 2394575']
['RU 2134755', 'SU 1652487', 'SU 742557']
['RU 2200420']
['RU 2255788', 'RU 2150218', 'RU 2119761']
['RU 2128640']
['RU 2355254']
['RU 2076485', 'RU 2199235', 'RU 2200425', 'RU 2000713', 'RU 2094002', 'RU 2000066']
['SU 446495', 'SU 1691360', 'RU 2121990']
['RU 2063370', 'RU 2159963']
['RU 2066682']
['RU 2123338']
['SU 399708', 'SU 590547', 'SU 983429']
['RU 2008176', 'RU 99126358', 'RU 2203172', 'SU \n1712135', 'SU 933370', 'SU 1230807']
['SU 1728755', 'SU 834480', 'RU 2149386', 'RU 2149389']
['RU 2068553', 'RU 2140625', 'RU 2176783', 'RU 2101364']
['RU 2137447']
['RU 2271814', 'RU 2185449', 'RU 2278689']
['RU 2107992']
['RU 2294117', 'RU 2456867']
['SU 1666527', 'SU 1761184']
['SU 821631']
['SU 311826']
['SU 1633321', 'RU 2017112']
['SU 1597159', 'SU 443666', 'SU 810202', 'RU 2007940

['SU 582253']
['SU 97613']
['RU 2146472', 'RU 2158514', 'RU 2125086', 'RU \n2008325']
['SU 1831213', 'RU 2012949']
['SU 1507265', 'SU 1530149']
['RU 2157521', 'SU 1035498']
['RU 2070016']
['RU 2353167']
['RU 2082646']
['RU 2186687', 'SU 1606346', 'SU 1177228']
['RU 2248155']
['SU 897877', 'RU 2071982', 'RU 2070592', 'RU 2044784', 'RU 2236474']
['RU 2023024', 'SU 1096943', 'RU 2030460']
['RU 2187607', 'RU 2194825', 'RU \n2179612']
['SU 1181305', 'SU 1824420', 'RU 2124039']
['RU 2060671']
['RU 2008143830', 'RU 2008135853', 'RU 2144217', 'RU 2339011']
['RU 2451407', 'RU 2380836', 'RU 2236090', 'RU 2285345']
['RU 2150683', 'RU 2020302']
['RU 2169015']
['SU 858790', 'SU 1041098']
['SU 254265']
['SU 659648', 'SU 998597', 'SU 1420070']
['SU 1161785', 'SU 468057']
['RU \n99104796']
['RU 2058111', 'RU \n\n2053712']
['RU 2007928', 'RU 2084171']
['SU 545611', 'SU 562534']
['RU 2107245']
['SU 717521', 'SU 1799457']
['RU 2038590', 'RU 2088914']
['RU 2091826', 'SU 1834586']
['RU 2161028']
['SU 14508

['SU 1', 'SU 1']
['RU 2004109517']
['RU 2178426']
['SU 681366']
['RU 2345727', 'RU 2332180', 'RU 2053805']
['SU 717241', 'SU 808710', 'SU 861762']
['SU 1121003', 'SU 1569017', 'SU 1837867']
['SU 3987731', 'SU 295852']
['RU 2182444']
['SU 958717']
['SU 1006297']
['RU 2118008', 'RU 2124246', 'RU 2035776', 'RU 1831722', 'SU 1767555']
['RU 2382356']
['RU 2331101', 'RU 2220443']
['SU 1022649', 'RU 2109463']
['RU 2204201']
['RU 2419279', 'SU 1521361']
['RU 2087506']
['RU 2024244', 'RU 2360688']
['SU 1814885']
['SU 671744', 'RU 2010103', 'SU 883488', 'SU 705119', 'SU 815314', 'SU 948296', 'SU 1104294']
['SU 1399239', 'SU 501908']
['SU 639962', 'RU 2125113', 'SU 834210']
['SU 779421', 'RU 2341585']
['SU 1194902', 'SU 639955', 'SU 1121305']
['SU 144694', 'SU 789637']
['RU 2078640', 'RU 2468919', 'SU 816790']
['RU 2176917']
['SU 259371', 'SU 701989', 'SU 931726']
['SU 1003648', 'RU 2155798', 'SU 859432']
['RU 2211154', 'SU 1826950']
['SU 782798', 'SU 984457', 'SU 279919']
['RU 2000103357', 'SU 3

['RU 2278551']
['SU 1588350', 'RU 96123717']
['RU \n\n2129969']
['RU 2035185', 'SU \n1398868', 'RU 1722502', 'RU 2067616', 'RU 2084233']
['RU 2175801']
['RU 2129675', 'SU 1206505', 'RU 2140585']
['SU 1141968']
['RU 2010136412']
['SU 413050', 'SU 967267', 'SU 1680557']
['RU 2038491']
['SU 862834']
['SU 447301', 'SU 1147595']
['SU 906508', 'RU 2055518']
['RU 2035719', 'SU 934382', 'SU 1665305']
['SU 131323', 'SU 433201']
['SU 400110']
['SU 803957', 'SU 929186']
['RU 2010108614']
['SU 941544', 'RU 2262586', 'RU 2132933', 'SU 1682535', 'SU 1126720', 'SU 1460423']
['SU 1807166', 'RU 2107127', 'SU \n\n1765292', 'RU 2176701', 'RU 2104367', 'SU 1707134']
['RU 95956', 'RU 2314666', 'RU 2423036', 'SU 1085538']
['RU 98117675', 'RU 2126447', 'RU 2077340', 'RU 2000111744']
['SU 832779']
['RU 2155141']
['RU 2000128036']
['RU 2219103']
['SU 127186', 'SU 165405', 'SU 451592']
['SU 325351', 'SU 909134', 'SU 1753750', 'SU \n138555', 'RU 2211311']
['RU 2006117780']
['RU 2312397', 'RU 2097906', 'RU 184072

['RU 2342392', 'RU 2342393', 'RU 23423395']
['SU 1577802', 'RU \n\n2072638', 'SU 1107350']
['RU 2331317', 'SU 1333289']
['RU 2153982']
['RU 2005137403']
['SU 240627', 'SU 375606', 'SU 407257']
['SU 290687']
['SU 75642', 'SU 698732', 'RU 2385786']
['SU 1296623']
['RU 2156645']
['RU 2168206']
['SU 474580']
['SU 1035247', 'SU 1038543', 'RU 2027867', 'RU 2044924']
['RU 2146494', 'RU 2202939']
['SU 299569', 'SU 543686', 'RU 2033471']
['SU 779615', 'RU 2033557']
['SU 536123', 'SU 631440']
['RU 2255788']
['RU 2316760', 'RU 2403562']
['RU 2248155', 'RU 2250741']
['RU 2406996', 'SU 972071', 'SU 1814694']
['RU 2011102', 'SU 1241000', 'SU 929952']
['SU 1258988', 'SU 591594', 'SU 1210074', 'SU 1203236', 'SU 973810']
['SU 398026']
['SU 564071', 'SU 489576']
['RU 2204833']
['RU 2013066', 'RU 2199241', 'RU 2197141', 'RU \n2198551', 'RU 2197123', 'RU 2194391', 'RU 2199235', 'RU \n2206242']
['RU 2356400']
['RU 2079454']
['RU 2198063', 'RU 2078391']
['SU \n\n\n412260', 'SU 544684', 'SU 916557', 'SU 1330

...

['SU 1224311']
['SU 278743']
['RU 2154348']
['SU 1684627']
['RU 2265435', 'RU 2291430', 'RU 2328989']
['RU 2132862', 'RU 2024578']
['RU 2107360']
['RU 2118187']
['RU 2314554', 'RU 2154847', 'RU 2065615']
['RU 2133956', 'RU \n2008652', 'RU 2149382']
['SU 1316922', 'SU 157932', 'SU 1806069']
['RU 2169122', 'RU 2134231']
['RU 20292666', 'RU 2145066', 'RU 2145065', 'RU 2087883', 'RU 2139509', 'RU 2104506']
['SU 695561', 'RU 2188832']
['SU 870264', 'SU 568580', 'SU 1697160', 'SU 1373607', 'RU 2116234']
['RU 2', 'RU 2', 'RU 2']
['RU 2070999', 'SU 1772457']
['RU 2001103', 'SU 1344247', 'RU 2043923']
['SU 754195', 'RU 2335463', 'RU 2303049', 'RU 2094728']
['RU 2271908', 'RU 2196030', 'RU 2277465']
['RU 75304', 'RU 2096024']
['RU 2099012']
['RU 2281665', 'RU 2278542']
['SU 553472']
['RU 2065216', 'RU 2116682', 'RU 2009556']
['SU 957881']
['SU \n1316637', 'RU 2197111', 'SU 1703039', 'RU 2000066']
['RU 2009109428']
['RU 2385713', 'RU 2294196', 'RU 2010101524']
['SU 188425', 'SU 120197', 'SU 48083

['SU 481929', 'SU 409262', 'SU 416717', 'RU 2020752']
['RU 7744', 'RU 2037736']
['RU 2005199', 'SU 1810599', 'SU 17137']
['SU 937356', 'SU 975593', 'SU 590268']
['RU 2036996']
['RU 2006770', 'RU 2247910', 'RU 2273812', 'RU 2084787', 'RU 2338980']
['RU 2329690', 'RU 2301582']
['RU 2124014']
['RU 2200267', 'SU 1224496', 'SU 629393']
['RU 2316026', 'SU 855586']
['SU 594887']
['RU 2018757', 'SU 1213300']
['SU 940755', 'SU 995769', 'SU 1099442']
['RU 2219501', 'RU 2215997']
['SU 972400']
['SU 100']
['SU 1542932', 'RU 2387621', 'RU 2400448', 'SU 1726442']
['RU 2156930', 'RU 2255485']
['SU 1710036', 'SU 1823799']
['RU 2097428', 'RU 2198179']
['SU 1042731', 'SU 1264903', 'SU 1463231']
['RU 2095285']
['RU 2148795', 'RU 2182713', 'RU 2046736']
['RU 2135175', 'RU 2158595']
['SU 572615']
['SU 1002328']
['RU 2152816', 'SU 1340777']
['RU 2267183']
['RU 2003107824']
['RU 2280386', 'RU 2003135186']
['SU 469172']
['SU 74759', 'SU 901756']
['RU 2186508', 'RU 2187948', 'RU 2197152', 'RU 2197871']
['SU 69

['RU 2170496']
['RU 2003120284', 'RU 2301600']
['RU 2213548']
['RU 2284114', 'RU 94034352', 'RU 2236138']
['RU 2193484', 'SU 1622133', 'SU 401653', 'RU 2067532']
['RU 2150630', 'SU 988574', 'RU 2044961', 'RU 2162562', 'RU 2147355', 'RU 2151059']
['RU 2158810', 'RU 2094958', 'RU 2079979']
['SU 1830371', 'SU 442976', 'SU 1188056']
['SU 613455']
['SU 857152']
['SU 1087727']
['SU 306739', 'SU 531881']
['RU 2127524', 'RU 2006117406']
['RU 2255788']
['SU 1411853', 'RU 2057760']
['SU 1634913', 'SU 430263', 'RU 2129681']
['SU 466210']
['SU 1193752', 'RU 2076434']
['SU 1819479', 'RU 2072569', 'RU 2080665', 'RU 2031460']
['SU 604046', 'RU 2003115596']
['SU 1296143']
['RU 2172067', 'RU 2253947']
['RU \n2007422', 'RU 2048816']
['SU 1587231', 'SU 735831']
['SU 768990', 'SU 1078089', 'SU 973852', 'SU 1581812', 'RU 2283959', 'RU 2337241']
['SU 850749', 'SU 612641']
['RU 2219804', 'RU 2221457']
['RU 2016693', 'RU 2219012', 'SU 1804945']
['SU 961']
['SU 1779364', 'RU 94045187']
['RU 2280397']
['RU 2154

['RU 99100641']
['SU 1471580', 'SU 1448709']
['RU 2131245', 'RU 2141319', 'RU 2142762']
['RU 2210766', 'SU 160031', 'SU 1742669', 'SU 1753334']
['RU 2143902', 'RU 2082322', 'SU 1235503', 'SU 1503831']
['SU 1047629', 'SU 52833', 'SU 990448', 'SU 1209388']
['RU 2265139', 'RU 2004850']
['SU 1767285', 'SU 1756734']
['RU 2227797']
['SU \n1011974', 'RU 2079079', 'RU 2049296']
['SU 388383', 'RU 2048520', 'RU 2116314', 'RU 2000066']
['RU 2005103588']
['SU 1072892', 'RU 2023509']
['RU \n\n2086225', 'SU 1627187']
['RU 2170740']
['RU 2373378', 'RU 2303121', 'RU 2242585', 'RU 2213848']
['RU 2166294']
['RU 2252654']
['RU 2287483', 'RU 2011102596']
['RU 2079166']
['RU 2280378', 'RU 2278600', 'SU 56163']
['RU 2051231', 'RU 2061398', 'RU 2077240']
['RU 2207281']
['SU 362002']
['RU 2243764']
['SU 196689', 'SU 1445824', 'SU 1794509', 'SU 778828']
['RU 2010117058', 'RU 2010105186']
['RU 2235118', 'RU 2259348']
['SU 1226370']
['RU 2241992']
['RU 2337373', 'RU 2296345', 'RU 2114444', 'RU 2402034']
['RU 206

['SU \n409434', 'SU 404956']
['RU 2113844', 'RU 2157183', 'RU 2161031', 'RU 2127582']
['SU 882714']
['SU 566172', 'SU \n990668']
['RU 2183761', 'RU 2183763']
['SU 729', 'SU 439', 'RU 2', 'RU 2']
['RU 2095717', 'SU 1760298', 'SU 545852', 'SU 787867', 'SU \n941837']
['SU 323912']
['RU 2261286']
['SU 383367']
['SU 1444716', 'SU 930274']
['SU 1398868']
['SU 1346472']
['RU 2301236']
['RU 2486215', 'RU 2481428', 'SU 1081139', 'SU 1142487']
['RU 2040522']
['RU 2195241', 'RU 2173549']
['RU 2070321', 'RU 2214835']
['SU 56163']
['SU 459531', 'RU 2237755', 'RU 2179203']
['RU 2207723']
['RU 2163871', 'RU 2074826', 'RU 2122239']
['RU 2004138984']
['RU 2203347', 'RU 2209138', 'RU 93016892', 'RU 2381106']
['SU \n\n311918']
['RU 2022024', 'SU 312876', 'SU 513630']
['RU 2309867', 'RU 2292286']
['RU 2285976', 'RU 2364984', 'RU 2393589']
['RU 2009104306']
['RU 2070811', 'RU 2045915', 'RU 2045915']
['RU 2047944', 'SU 1553936']
['RU 2137066', 'RU 2137067']
['RU 2255788']
['SU 126836', 'RU 2180395', 'RU 218

In [105]:
strange = []
for k in diff:
    v = regexed2[k]
    for s in v:
        if len(s.split()[1]) < 4:
            print(s)
            strange.append(s)

RU 2
RU 2
SU 586
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
SU 92
RU 2
RU 2
RU 922
RU 2
RU 111
RU 10
SU 462
SU 273
RU 2
RU 2
RU 2
SU 196
SU 236
SU 293
SU 302
SU 485
SU 899
SU 929
RU 93
RU 2
RU 2
SU 1
SU 1
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
SU 1
SU 97
SU 190
SU 543
SU 563
SU 751
SU 765
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
SU 629
RU 2
SU 1
SU 912
SU 324
SU 1
SU 920
SU 1
RU 95
RU 2
RU 2
RU 2
RU 2
RU 2
SU 140
RU 2
RU 2
RU 2
SU 1
SU 1
SU 437
SU 1
SU 1
RU 2
RU 2
SU 1
SU 120
SU 823
SU 165
RU 2
SU 1
SU 1
RU 2
RU 95
SU 913
RU 2
SU 732
SU 525
SU 1
SU 1
SU 895
RU 2
RU 2
RU 2
RU 2
RU 108
SU 1
RU 2
RU 2
SU 70
RU 2
SU 1
SU 1
SU 1
RU 2
SU 898
RU 1
RU 
2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
SU 665
RU 2
RU 2
RU 2
RU 2
SU 259
SU 1
RU 2
RU 2
RU 99
RU 2
RU 212
SU 1
RU 2
RU 2
SU 1
RU 39
RU 2
RU 94
RU 2
RU 2
RU 2
RU 2
RU 95
SU 1
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
RU 2
SU 1
SU 1
SU 1
SU 96
SU 1
RU 2
RU 2
RU 5
RU 2
SU 105
SU 611
SU 719
RU 94
RU 99

In [106]:
len(strange)

2197

In [100]:
v

['RU 2455739 C2', 'RU 2230410 C1', 'RU 113426 U1']

In [63]:
lens = 0
for k,v in regexed.items():
    lens += len(v)
print(lens)

732164


In [108]:
top10 = db.patents.find({'doc-number': {'$regex': '^[0]{0,}961$' }}).skip(0).limit(10)
pprint(list(top10))
print(top10.count())


[{'_id': ObjectId('5984b714b6b1131bd76384f1'),
  'claims': 'уплотнение подшипник качение, выполнять в вид шайба из упругий '
            'материал, армированный металлический кольцо, отличаться то, что '
            'поперечный профиль периферийный наружный зона выполнять с '
            'возможность осуществление функция собачка и образовывать скос с '
            'внутренний сторона уплотнение и поднутрение с наружный сторона, '
            'иметь глубина и сечение, достаточный для обеспечение упругий '
            'отклонение периферийный наружный участок при вставление '
            'уплотнение в канавка кольцо, предназначать для уплотнение.\n',
  'claims_raw': 'уплотнение подшипника качения, выполненное в виде шайбы из '
                'упругого материала, армированной металлическим кольцом, '
                'отличающееся тем, что поперечный профиль периферийной '
                'наружной зоны выполнен с возможностью осуществления функции '
                'собачки и образован 

1


# Get w2v

Get sentences for w2v model and tokenize on the fly

In [ ]:
# iter only over 

for sentence in sent_tokenize(text):
    document.append(list(tokenize(sentence, self.stop_words)))
